<a href="https://colab.research.google.com/github/nitsundon/100DaysofML/blob/main/Day1/RNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [13]:
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
import plotly.express as px

In [2]:
df= pd.read_pickle("/content/drive/MyDrive/Libraries/pickle/preprocessed_demand_df.pkl")

In [12]:
df1=df.interpolate().set_index('datetime')
scaler = MinMaxScaler()
data_scaled = scaler.fit_transform(df1)
data_scaled_df = pd.DataFrame(data_scaled, columns=df1.columns, index=df1.index)
data_scaled_df.head()

demand
datetime                     
2022-01-01 00:00:00  0.326487
2022-01-01 00:15:00  0.325481
2022-01-01 00:30:00  0.320685
2022-01-01 00:45:00  0.327153
2022-01-01 01:00:00  0.328219

In [16]:
fig = px.line(data_scaled_df,  y=["demand"],
              title="State Demand Over Time (15-Min Blocks)",
              labels={"Timestamp": "Time", "Demand_MW": "Demand (MW)"},
              template="simple_white")  # Optional: Use "seaborn" or "simple_white" theme

# Show interactive graph
fig.show()

In [17]:
def create_sequences(data, seq_length):
    x, y = [], []
    for i in range(len(data) - seq_length):
        x.append(data[i:i+seq_length])
        y.append(data[i+seq_length])
    return np.array(x), np.array(y)

In [ ]:
import numpy as np
seq_length = 24  # assuming hourly data, this uses past 24 hours
X, y = create_sequences(data_scaled[-(96*365*2):], seq_length)
X,y

In [27]:
split = int(0.8 * len(X))
X_train, X_test = X[:split], X[split:]
y_train, y_test = y[:split], y[split:]


In [28]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import SimpleRNN, Dense
from sklearn.preprocessing import MinMaxScaler
# Define the RNN model
model = Sequential()
model.add(SimpleRNN(50, activation='relu', input_shape=(seq_length, 1)))
model.add(Dense(1))
model.compile(optimizer='adam', loss='mse')

/usr/local/lib/python3.11/dist-packages/keras/src/layers/rnn/rnn.py:200: UserWarning:

Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.



In [36]:
predicted = model.predict(X_test)
predicted_actual = scaler.inverse_transform(predicted)
y_test_actual = scaler.inverse_transform(y_test)


438/438 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step


In [37]:
from sklearn.metrics import mean_absolute_percentage_error

# Calculate MAPE
mape = mean_absolute_percentage_error(y_test_actual, predicted_actual)
print(f'MAPE: {mape * 100:.2f}%')

MAPE: 0.58%


In [ ]:

import matplotlib.pyplot as plt
# Start with the last available sequence from the full dataset
last_sequence = data_scaled[-seq_length:]  # shape: (24, 1)
forecast_steps = 24  # e.g., forecast next 24 hours
forecast = []

current_sequence = last_sequence.copy()

for _ in range(forecast_steps):
    pred = model.predict(current_sequence.reshape(1, seq_length, 1), verbose=0)
    forecast.append(pred[0, 0])
    # update current_sequence by appending the prediction and removing the first value
    current_sequence = np.append(current_sequence[1:], [[pred[0, 0]]], axis=0)

# Inverse transform to get actual MW values
forecast_actual = scaler.inverse_transform(np.array(forecast).reshape(-1, 1))
historical_data = scaler.inverse_transform(data_scaled)


In [41]:
import plotly.graph_objects as go

# Historical and Forecast Data
historical_data = scaler.inverse_transform(data_scaled)
forecast_x = list(range(len(historical_data), len(historical_data) + forecast_steps))

# Create Plotly figure
fig = go.Figure()

# Add historical demand trace
fig.add_trace(go.Scatter(
    x=list(range(len(historical_data))),
    y=historical_data.flatten(),
    mode='lines',
    name='Historical Demand',
    line=dict(color='blue')
))

# Add forecast trace
fig.add_trace(go.Scatter(
    x=forecast_x,
    y=forecast_actual.flatten(),
    mode='lines+markers',
    name='Forecast Demand',
    line=dict(color='orange', dash='dash')
))

# Layout settings
fig.update_layout(
    title='Power Demand Forecast (RNN)',
    xaxis_title='Time Step',
    yaxis_title='Demand (MW)',
    template='plotly_white',
    legend=dict(x=0.01, y=0.99),
    hovermode='x unified'
)

fig.show()
